# Flask adventures

## Any port in a storm

A port is like a numbered door in a giant hotel. Each Flask app running on the server needs to have a unique port number. Let's assign each user of the soupboat a unique port numbers for (personal) testing... In the end we may want to use a single flask server running on a single port, but for now, and for testing, it's important that each user can temporarily run a server and see their results independently from everyone else.

In [2]:
import os

USER = os.environ.get("USER")
print (f"You user name is {USER}")

You user name is manetta


In [3]:
USERS = "chae gi ohjian alnik supi flem carmen grgr kamo mirischoeb mitsa kimberley murtaugh manetta cristina"
USERS = USERS.split()

In [4]:
port = 9080
USER_PORTS = {}
for user in USERS:
    USER_PORTS[user] = port
    port += 1
USER_PORTS

{'chae': 9080,
 'gi': 9081,
 'ohjian': 9082,
 'alnik': 9083,
 'supi': 9084,
 'flem': 9085,
 'carmen': 9086,
 'grgr': 9087,
 'kamo': 9088,
 'mirischoeb': 9089,
 'mitsa': 9090,
 'kimberley': 9091,
 'murtaugh': 9092,
 'manetta': 9093,
 'cristina': 9094}

In [5]:
PORT = USER_PORTS[USER]
print (f"Hey {USER} your port is {PORT}")

Hey manetta your port is 9093


In [6]:
for USER, PORT in USER_PORTS.items():
    print(f"https://hub.xpub.nl/soupboat/{USER}/api/")

https://hub.xpub.nl/soupboat/chae/api/
https://hub.xpub.nl/soupboat/gi/api/
https://hub.xpub.nl/soupboat/ohjian/api/
https://hub.xpub.nl/soupboat/alnik/api/
https://hub.xpub.nl/soupboat/supi/api/
https://hub.xpub.nl/soupboat/flem/api/
https://hub.xpub.nl/soupboat/carmen/api/
https://hub.xpub.nl/soupboat/grgr/api/
https://hub.xpub.nl/soupboat/kamo/api/
https://hub.xpub.nl/soupboat/mirischoeb/api/
https://hub.xpub.nl/soupboat/mitsa/api/
https://hub.xpub.nl/soupboat/kimberley/api/
https://hub.xpub.nl/soupboat/murtaugh/api/
https://hub.xpub.nl/soupboat/manetta/api/
https://hub.xpub.nl/soupboat/cristina/api/


## "A minimal application"

https://flask.palletsprojects.com/en/2.0.x/quickstart/

This is the "hello world" of Flask. NB: It's adapted to run directly (with app.run) and notice that the PORT variable connects it to YOUR PERSONAL PORT. 

In Flask a function is a "route" ... sometimes called a view. The @app.route is called a *decorator* : it modifies the function (hello_world in this case) to connect it to the URL patter, in this case your user name + /api. Each time a user goes to the matching URL, this function is called (once for each individual viewer) and the response is served.

**REMEMBER TO STOP THE CELL** app.run runs forever (serving requests until you STOP it). If you forget, you will see that other cells in the notebook are blocked until you stop this one.

To stop a cell: you can either press the STOP button (the square icon) in the toolbar above the notebook, or else use the keyboard (press Esc, then **I** twice to **Interrupt**).

In [13]:
from flask import Flask

app = Flask(__name__)

@app.route(f"/~{USER}/api/")
def hello_world():
    return "<h1>Hello to my World!</h1>"

app.run(port=PORT)

 * Serving Flask app '__main__' (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:9093/ (Press CTRL+C to quit)
127.0.0.1 - - [22/Nov/2021 11:50:57] "GET /~manetta/api/ HTTP/1.0" 200 -


### BONUS (technical details, which you can skip for now if it's too much, in the next step we make a nicer solution)

At the moment, there's not a public URL for your flask app. That's because the URL https://hub.xpub.nl/soupboat/ is connected to port 80 (the nginx server running on the soupboat). Other ports are not public (unless we also setup a "reverse proxy" for them in soupboat's nginx... See the next step!). **BUT** the soupboat does have an IP address on the school's network, and when you are also on the schools network, you can address the soupboat **directly** (ie not via areverse proxy trick) and so you **do** have access to other ports, simply by adding them after the ip address, like 145.100.100.100:1234 (port 1234). If you look at the IP addresses of the soupboat, can you figure out where to find your Flask app. (Unfortuntely, the "route" that the app gets in this case is different, so you'll get a 404 error, look at the error (in the messages displayed here in the notebook, to see what route the app is receiving and try making another "route" function to handle it.

In [1]:
!ip address

1: lo: <LOOPBACK,UP,LOWER_UP> mtu 65536 qdisc noqueue state UNKNOWN group default qlen 1000
    link/loopback 00:00:00:00:00:00 brd 00:00:00:00:00:00
    inet 127.0.0.1/8 scope host lo
       valid_lft forever preferred_lft forever
    inet6 ::1/128 scope host 
       valid_lft forever preferred_lft forever
2: eth0: <BROADCAST,MULTICAST,UP,LOWER_UP> mtu 1500 qdisc mq state UP group default qlen 1000
    link/ether e4:5f:01:0e:ef:2f brd ff:ff:ff:ff:ff:ff
    inet 145.24.131.145/24 brd 145.24.131.255 scope global dynamic noprefixroute eth0
       valid_lft 180463sec preferred_lft 148063sec
    inet6 fe80::af0e:2964:30f0:3a1b/64 scope link 
       valid_lft forever preferred_lft forever
3: wlan0: <BROADCAST,MULTICAST> mtu 1500 qdisc noop state DOWN group default qlen 1000
    link/ether e4:5f:01:0e:ef:30 brd ff:ff:ff:ff:ff:ff
4: hub: <POINTOPOINT,MULTICAST,NOARP,UP,LOWER_UP> mtu 1500 qdisc pfifo_fast state UNKNOWN group default qlen 500
    link/none 
    inet 10.0.0.13/24 scope global hu

## Giving a public entryway to your (private) door...

Now that we have a unique door, let's fix them and give a public address to this private (to the school's network) door...


in /etc/nginx/sites-available/default


```
location ^~ /~USER/api/ { proxy_pass http://localhost:PORT; }
```

In [6]:
for user, port in USER_PORTS.items():
    print (f"""location ^~ /~{user}/api/ {{ proxy_pass http://localhost:{port}; }}""")

location ^~ /~chae/api/ { proxy_pass http://localhost:9080; }
location ^~ /~gi/api/ { proxy_pass http://localhost:9081; }
location ^~ /~ohjian/api/ { proxy_pass http://localhost:9082; }
location ^~ /~alnik/api/ { proxy_pass http://localhost:9083; }
location ^~ /~supi/api/ { proxy_pass http://localhost:9084; }
location ^~ /~flem/api/ { proxy_pass http://localhost:9085; }
location ^~ /~carmen/api/ { proxy_pass http://localhost:9086; }
location ^~ /~grgr/api/ { proxy_pass http://localhost:9087; }
location ^~ /~kamo/api/ { proxy_pass http://localhost:9088; }
location ^~ /~mirischoeb/api/ { proxy_pass http://localhost:9089; }
location ^~ /~mitsa/api/ { proxy_pass http://localhost:9090; }
location ^~ /~kimberley/api/ { proxy_pass http://localhost:9091; }
location ^~ /~murtaugh/api/ { proxy_pass http://localhost:9092; }
location ^~ /~manetta/api/ { proxy_pass http://localhost:9093; }
location ^~ /~cristina/api/ { proxy_pass http://localhost:9094; }


In [7]:
print (f"https://hub.xpub.nl/soupboat/~{USER}/api/")

https://hub.xpub.nl/soupboat/~manetta/api/


404: Web server doesn't know the address (proxy pass not yet in place)... recheck the "default" file (nginx settings)

502: Bad gateway? *This is better* ... proxy_pass is working, but the server knocked on the door (port) but no one answered. Now you just need to make sure your Flask is running and listening on that port...

## Web 1.0 Interactivity: the humble &lt;form&gt;

Methods, GET vs POST and FORMs

https://flask.palletsprojects.com/en/2.0.x/quickstart/#http-methods

In [ ]:
from flask import Flask, request

app = Flask(__name__)

@app.route(f'/~{USER}/api/')
def login():
    text = ""
    text = request.values.get('message', '')
    return f"""
    <form>
    <textarea name="message" autofocus placeholder="type your message" style="width: 100%; height: 10em">{text}</textarea>
    <input type="submit">
    </form>"""

app.run(port=PORT)

## Customize the transformation

Modify the Flask code above with a transformation (for instance make the text uppercase)

Remember, to STOP and RESTART the server to see changes to the code.

Next steps:

* Use a function to modify the text (in this way you can separate the Flask code from your text transformation).
* Put the function in an external .py file and use **import** to use it in the flask code.

## Cross posting

https://developer.mozilla.org/en-US/docs/Web/HTML/Element/details

When everyone has a working text tranformer, try the following server to introduce some cross-posting!

Be sure to add your transformation code from above into the code below...

In [ ]:
from flask import Flask, request
import random

app = Flask(__name__)

@app.route(f'/~{USER}/api/', methods=['GET', 'POST'])
def login():
    text = ""
    if request.method == 'POST':
        text = request.form['message']
    output = ""
    random_user = random.choice(USERS)
    for user in USERS:
        o = " open" if user == random_user else ""
        output += f"""
        <details{o}>
        <summary>send to {user}</summary>
        <form action="/soupboat/~{user}/api/" method="post">
            <textarea name="message" autofocus placeholder="type your message" style="width: 100%; height: 10em">{text}</textarea>
            <input type="submit">
        </form>
        </details>"""
    
    return output

app.run(port=PORT)

---
## Some other examples


### Simple chat room

A Flask server is shared between all the different users who visit the URL. (This, unlike javascript in a page that runs for each user individually in their respective and isolated browser). A global variable can provide a simple way to share information **between different users**. REmember though, this "state" is ephemeral, it's forgotten when the server stops; to make it permanent you would use a file, or perhaps eventually another service/server/API like a database. But to start, keep it simple...

In [ ]:
from flask import Flask, request

app = Flask(__name__)

messages = []

@app.route(f'/~{USER}/api/', methods=['GET', 'POST'])
def login():
    if request.method == 'POST':
        messages.append(request.form['message'])
    ret = ''
    for message in messages:
        ret += (f"""<div>{message}</div>\n""")
    ret += """
        <form method="post">
        <input type="text" name="message" autofocus placeholder="type your message">
        <input type="submit">
        </form>"""
    return ret

app.run(port=PORT)

### adding an API to your API

Maybe you'd like to make a static page that uses javascript to visualize the chat messages ?!

We can add a new route (indes.json) that just dumps the messages in a JSON format...

Making JSON responses is really easy with Flask, just return a dictionary...

https://flask.palletsprojects.com/en/2.0.x/quickstart/#apis-with-json


In [ ]:
from flask import Flask, request
import json

app = Flask(__name__)

messages = []

@app.route(f'/~{USER}/api/', methods=['GET', 'POST'])
def login():
    if request.method == 'POST':
        messages.append(request.form['message'])
    ret = ''
    for message in messages:
        ret += (f"""<div>{message}</div>\n""")
    ret += """
        <form method="post">
        <input type="text" name="message" autofocus placeholder="type your message">
        <input type="submit">
        </form>"""
    return ret

@app.route('/~murtaugh/api/index.json', methods=['GET', 'POST'])
def api():
    return {'messages': messages}

app.run(port=PORT)

### Other info in the Request object

More than just the form contents are sent when you submit a form. In fact *every* request, including GETs, contains lots of other information about the request in the so-called "Request header"...

https://developer.mozilla.org/en-US/docs/Glossary/Request_header

https://developer.mozilla.org/en-US/docs/Web/HTTP/Headers#request_context

https://flask.palletsprojects.com/en/2.0.x/quickstart/#the-request-object

In [ ]:
from flask import Flask, request

app = Flask(__name__)

messages = []

@app.route(f'/~{USER}/api/', methods=['GET', 'POST'])
def login():
    if request.method == 'POST':
        messages.append((request.user_agent, request.form['message']))
    ret = ''
    for user_agent, message in messages:
        ret += (f"""<div>{user_agent}: {message}</div>\n""")
    ret += """
        <form method="post">
        <input type="text" name="message" autofocus placeholder="type your message">
        <input type="submit">
        </form>"""
    return ret

app.run(port=PORT)

### Adding a number drop down

In [ ]:
from flask import Flask, request

app = Flask(__name__)

messages = []
for i in range(10):
    messages.append('')

@app.route(f'/~{USER}/api/', methods=['GET', 'POST'])
def login():
    if request.method == 'POST':
        slot = int(request.form['slot'])
        messages[slot-1] = request.form['message']
    ret = ''
    for i, m in enumerate(messages):
        ret += (f"""<div class="slot{i+1}">{m}</div>\n""")
    ret += """
        <form method="post">
        <input type="text" name="message" autofocus placeholder="type your message">
        <select name="slot">
            <option>1</option>
            <option>2</option>
            <option>3</option>
            <option>4</option>
            <option>5</option>
        </select>
        <input type="submit">
        </form>"""
    return ret

app.run(port=PORT)